Student: Duncan Ferguson <br>
Student Id: 871641260 <br>
Class: Comp 4431-1 <br>
Assignment: Assignment 3 <br>
Date: 11/20/2021 <br>

You are to apply the following techniques to mine this data set:
- Association Rules
- Decision tree Classification
- Naive Bayes Classification
- kmeans and dbscan clustering

Also, you are to use Principle Component Analysis to reduce the number of attributes
(aka features)

Please answer the following questions:

1. What can you deduce from the data set? (in otherwords, what attribute values are indicative of "success")
2. Which mining techniques yielded the best results for what? How do you define "best results"? Please
include tables and/or graphs to justify your statement

Note: While numeric data is desired for classification/clustering, you need strings that look like market basket
data (sets of item names) for Association Rules. Numeric data can be grouped into names like
"lowValue, midValue, midValue, mediumHighValue, highValue" etc. See the following code for possible
way of doing this (not necessarily the best):

What to turn in:
- a pdf file with the answers to these three questions
- Your code used to answer these questions


In [290]:
# Importing Standard Libraries
import pandas as pd
import numpy as np

# Sklearn Libraries
from sklearn import tree
from sklearn.model_selection import train_test_split
from sklearn.metrics import *
from sklearn.naive_bayes import *
from sklearn.cluster import KMeans, DBSCAN
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler

# Importing mlxtend Libraries
from mlxtend.frequent_patterns import apriori, association_rules
from mlxtend.preprocessing import TransactionEncoder

# Graphing Libraries
import matplotlib.pyplot as plt
import seaborn as sns

In [291]:
# Setting up view options
pd.set_option('display.max_columns', None)
pd.set_option('max_columns', None)
pd.set_option('max_rows', None)
pd.options.display.width = 0   #


In [292]:
# Importing the Data Set
df =  pd.read_csv("bank.csv")
# df =  pd.read_csv("bank-full.csv")
df.head()

# Establishing copies for running through the different scrubs
df_a = df.copy()
df_b = df.copy()

### Association Rules Data Mining
First Cleaning up the data and creating categories

In [293]:
for index, row in df_a.iterrows():
	if row['balance'] < 0:
		row['balance'] = 'inDebt'
	else:
		row['balance'] = 'notInDebt'

# Creating Categories for balance
df_a.loc[(df_a['balance'] >= 10000), 'balanceSummary'] = 'veryPositive'
df_a.loc[((df_a['balance'] < 0) & (df_a['balance'] >= -10000)), 'balanceSummary'] = 'negative'
df_a.loc[((df_a['balance'] < 10000) & (df_a['balance'] >= 0)), 'balanceSummary'] = 'positive'
df_a.loc[df_a['balance'] < -500, 'balanceSummary'] = 'veryNegative'

# Creating Categories for ages
df_a.loc[((df_a['age'] < 25) & (df_a['age'] >= 0)),  'ageBand'] = 'ageBand1'
df_a.loc[((df_a['age'] < 30) & (df_a['age'] >= 25)), 'ageBand'] = 'ageBand2'
df_a.loc[((df_a['age'] < 40) & (df_a['age'] >= 30)), 'ageBand'] = 'ageBand3'
df_a.loc[((df_a['age'] < 50) & (df_a['age'] >= 40)), 'ageBand'] = 'ageBand4'
df_a.loc[((df_a['age'] < 120) & (df_a['age'] >= 50)),'ageBand'] = 'ageBand5'

# Creating Categories for default
df_a.loc[(df_a['default'] == 'no'), 'defaultValue'] = 'defaultNo'
df_a.loc[(df_a['default'] == 'yes'), 'defaultValue'] = 'defaultYes'

# Creating Categories for Housing
df_a.loc[(df_a['housing'] == 'no'), 'housingVal'] = 'houseNo'
df_a.loc[(df_a['housing'] == 'yes'), 'housingVal'] = 'houseYes'

# Creating Categories for Loans
df_a.loc[(df_a['loan'] == 'no'), 'loanVal'] = 'loanNo'
df_a.loc[(df_a['loan'] == 'yes'), 'loanVal'] = 'loanYes'

Displaying Data with new categories

In [294]:
df_a.head(10)

age            job  marital  education default  balance housing loan  \
0   30     unemployed  married    primary      no     1787      no   no   
1   33       services  married  secondary      no     4789     yes  yes   
2   35     management   single   tertiary      no     1350     yes   no   
3   30     management  married   tertiary      no     1476     yes  yes   
4   59    blue-collar  married  secondary      no        0     yes   no   
5   35     management   single   tertiary      no      747      no   no   
6   36  self-employed  married   tertiary      no      307     yes   no   
7   39     technician  married  secondary      no      147     yes   no   
8   41   entrepreneur  married   tertiary      no      221     yes   no   
9   43       services  married    primary      no      -88     yes  yes   

    contact  day month  duration  campaign  pdays  previous poutcome   y  \
0  cellular   19   oct        79         1     -1         0  unknown  no   
1  cellular   11   may       220         1    339         4  failure  no   
2  cellular   16   apr       185         1    330         1  failure  no   
3   unknown    3   jun       199         4     -1         0  unknown  no   
4   unknown    5   may       226         1     -1         0  unknown  no   
5  cellular   23   feb       141         2    176         3  failure  no   
6  cellular   14   may       341         1    330         2    other  no   
7  cellular    6   may       151         2     -1         0  unknown  no   
8   unknown   14   may        57         2     -1         0  unknown  no   
9  cellular   17   apr       313         1    147         2  failure  no   

  balanceSummary   ageBand defaultValue housingVal  loanVal  
0       positive  ageBand3    defaultNo    houseNo   loanNo  
1       positive  ageBand3    defaultNo   houseYes  loanYes  
2       positive  ageBand3    defaultNo   houseYes   loanNo  
3       positive  ageBand3    defaultNo   houseYes  loanYes  
4       positive  ageBand5    defaultNo   houseYes   loanNo  
5       positive  ageBand3    defaultNo    houseNo   loanNo  
6       positive  ageBand3    defaultNo   houseYes   loanNo  
7       positive  ageBand3    defaultNo   houseYes   loanNo  
8       positive  ageBand4    defaultNo   houseYes   loanNo  
9       negative  ageBand4    defaultNo   houseYes  loanYes

Dropping data that is not in a string

In [295]:
df_a = df_a.drop('age',axis=1)
df_a = df_a.drop('day',axis=1)
df_a = df_a.drop('duration',axis=1)
df_a = df_a.drop('balance',axis=1)
df_a = df_a.drop('campaign',axis=1)
df_a = df_a.drop('previous',axis=1)
df_a = df_a.drop('default',axis=1)
df_a = df_a.drop('housing',axis=1)
df_a = df_a.drop('loan',axis=1)
df_a = df_a.drop('pdays',axis=1)

Displaying Final Data to be interpreted

In [296]:
df_a.head(10)

job  marital  education   contact month poutcome   y  \
0     unemployed  married    primary  cellular   oct  unknown  no   
1       services  married  secondary  cellular   may  failure  no   
2     management   single   tertiary  cellular   apr  failure  no   
3     management  married   tertiary   unknown   jun  unknown  no   
4    blue-collar  married  secondary   unknown   may  unknown  no   
5     management   single   tertiary  cellular   feb  failure  no   
6  self-employed  married   tertiary  cellular   may    other  no   
7     technician  married  secondary  cellular   may  unknown  no   
8   entrepreneur  married   tertiary   unknown   may  unknown  no   
9       services  married    primary  cellular   apr  failure  no   

  balanceSummary   ageBand defaultValue housingVal  loanVal  
0       positive  ageBand3    defaultNo    houseNo   loanNo  
1       positive  ageBand3    defaultNo   houseYes  loanYes  
2       positive  ageBand3    defaultNo   houseYes   loanNo  
3       positive  ageBand3    defaultNo   houseYes  loanYes  
4       positive  ageBand5    defaultNo   houseYes   loanNo  
5       positive  ageBand3    defaultNo    houseNo   loanNo  
6       positive  ageBand3    defaultNo   houseYes   loanNo  
7       positive  ageBand3    defaultNo   houseYes   loanNo  
8       positive  ageBand4    defaultNo   houseYes   loanNo  
9       negative  ageBand4    defaultNo   houseYes  loanYes

Displaying all Unique Values

In [297]:
for col in df_a:
    print(col, ":", df_a[col].unique())

job : ['unemployed' 'services' 'management' 'blue-collar' 'self-employed'
 'technician' 'entrepreneur' 'admin.' 'student' 'housemaid' 'retired'
 'unknown']
marital : ['married' 'single' 'divorced']
education : ['primary' 'secondary' 'tertiary' 'unknown']
contact : ['cellular' 'unknown' 'telephone']
month : ['oct' 'may' 'apr' 'jun' 'feb' 'aug' 'jan' 'jul' 'nov' 'sep' 'mar' 'dec']
poutcome : ['unknown' 'failure' 'other' 'success']
y : ['no' 'yes']
balanceSummary : ['positive' 'negative' 'veryPositive' 'veryNegative']
ageBand : ['ageBand3' 'ageBand5' 'ageBand4' 'ageBand1' 'ageBand2']
defaultValue : ['defaultNo' 'defaultYes']
housingVal : ['houseNo' 'houseYes']
loanVal : ['loanNo' 'loanYes']


Creating a transact 1 hot boolean encoded numpy array

In [299]:
# Turning df_a into a list of lists
df_a_list = df_a.to_numpy()

# Transforming into 1 hot boolean encoded numpy array
te = TransactionEncoder()
te_ary = te.fit(df_a_list).transform(df_a_list)
df_a_transformed = pd.DataFrame(te_ary, columns=te.columns_)
df_a_transformed

admin.  ageBand1  ageBand2  ageBand3  ageBand4  ageBand5    apr    aug  \
0      False     False     False      True     False     False  False  False   
1      False     False     False      True     False     False  False  False   
2      False     False     False      True     False     False   True  False   
3      False     False     False      True     False     False  False  False   
4      False     False     False     False     False      True  False  False   
5      False     False     False      True     False     False  False  False   
6      False     False     False      True     False     False  False  False   
7      False     False     False      True     False     False  False  False   
8      False     False     False     False      True     False  False  False   
9      False     False     False     False      True     False   True  False   
10     False     False     False      True     False     False  False  False   
11      True     False     False     False      True     False   True  False   
12     False     False     False      True     False     False  False   True   
13     False      True     False     False     False     False   True  False   
14     False     False     False      True     False     False  False  False   
15     False     False     False     False      True     False  False   True   
16     False     False     False     False     False      True  False   True   
17      True     False     False      True     False     False   True  False   
18     False     False      True     False     False     False  False  False   
19     False     False     False      True     False     False  False  False   
20     False     False     False      True     False     False  False  False   
21     False     False     False     False      True     False  False  False   
22     False     False     False     False      True     False  False  False   
23     False     False     False     False      True     False  False  False   
24     False     False      True     False     False     False  False  False   
25     False     False     False     False      True     False  False  False   
26     False     False     False     False     False      True  False  False   
27     False     False     False     False     False      True  False   True   
28     False     False     False     False     False      True  False  False   
29      True     False     False     False     False      True  False   True   
30     False     False     False     False     False      True  False  False   
31     False     False     False      True     False     False  False   True   
32     False     False     False     False     False      True  False  False   
33     False     False     False      True     False     False  False   True   
34     False     False     False     False      True     False  False   True   
35      True     False     False     False      True     False  False  False   
36     False     False     False     False     False      True  False  False   
37     False     False     False      True     False     False  False  False   
38     False     False     False      True     False     False  False  False   
39     False      True     False     False     False     False  False  False   
40     False     False     False      True     False     False  False  False   
41     False     False     False      True     False     False  False   True   
42     False     False     False     False     False      True  False  False   
43     False     False     False      True     False     False  False  False   
44     False     False     False      True     False     False  False  False   
45     False     False     False      True     False     False  False  False   
46     False     False     False     False     False      True  False  False   
47     False     False      True     False     False     False  False  False   
48     False     False     False      True     False     False  False  False   
49    

Creating a function for the apriori Algorithm so that it can easily be manipulated later for analysis

In [ ]:
def run_apriori(df, min_support_feed=0.02, min_threshold_feed=0.2, lift=1.1):
    """This function runs through the apriori algorithm taking in min support
    min threshold which is confidence and min lift. It returns association rules and frequent items"""
    freq_items = apriori(df, min_support=min_support_feed, use_colnames=True)
    freq_items['length'] = freq_items['itemsets'].apply(lambda x: len(x))
    freq_items.sort_values(["support", "length"], inplace=True, ascending=False)
    rules = association_rules(freq_items, metric="confidence", min_threshold=min_threshold_feed)
    if lift is not None:
        asso_rules = rules[rules["lift"] >= lift].copy()
    else:
        asso_rules = rules
    asso_rules.sort_values(["lift"], inplace=True, ascending=False)
    return asso_rules, freq_items

In [ ]:
df_a_associations, df_a_freq_items  = run_apriori(df_a_transformed, 0.02, 0.3, None)
df_a_associations

In [ ]:
df_a_freq_items

Looking at the association rules we notice a few interesting things
#### TODO
Write up the rules that are interesting